In [1]:
cotacoes = "/home/marcos/Documents/PricePrediction/COTAHIST_A"
anos = ["2010","2011","2012","2013","2014","2015", "2016", "2017", "2018", "2019"]
# anos = ["2006","2005","2007","2008","2009"]

vet = []
datas_pregoes = []

for ano in anos:
    with open(cotacoes + ano + ".TXT") as cot:
        for line in cot:
            vet.append(line)

In [2]:
import dateutil.parser
import datetime

def extract_data(line):
    cod_negociacao = line[12:24].replace(" ", "")
    data_pregao = line[2:10]
    
    preco_abertura = to_float(line[57:69].lstrip('0'))
    preco_max = to_float(line[69:82].lstrip('0'))
    preco_min = to_float(line[83:95].lstrip('0'))
    preco_medio = to_float(line[96:108].lstrip('0'))
    preco_ultimo_negocio = to_float(line[108:121].lstrip('0'))
    
    numero_negociacoes = int(line[147:152]) if len(line[147:152]) > 0 else 0
    quantidade_titulos_negociados = int(line[152:170].lstrip('0')) if len(line[152:170].lstrip('0')) > 0 else 0
    volume_titulos_negociados = int(line[170:188].lstrip('0')) if len(line[170:188].lstrip('0')) > 0 else 0
    
    if preco_abertura > 0:
        variacao = 100 * ((preco_ultimo_negocio - preco_abertura) / preco_abertura)
    else:
        variacao = 0
    
    data = {dateutil.parser.parse(data_pregao) : [ preco_abertura, preco_max, preco_min, preco_medio, 
                             preco_ultimo_negocio, numero_negociacoes, quantidade_titulos_negociados,
                             volume_titulos_negociados, variacao]}
    
    if cod_negociacao in papeis:
        papeis[cod_negociacao].update(data)
    else:
        papeis[cod_negociacao] = {}
        papeis[cod_negociacao].update(data)
        
    datas_pregoes.append(dateutil.parser.parse(data_pregao)) if dateutil.parser.parse(data_pregao) not in datas_pregoes else None

def to_float(str_number):
    """
    Converte numero no formato xxyy para xx.yy
    """
    if len(str_number) < 1:
        return 0
    
    numero = str_number[-1]
    
    if len(str_number) > 1:
        numero = str_number[-2] + numero
    
    numero = int(numero) / 100
    
    if len(str_number[0:-2]) > 0:
        numero = numero + int(str_number[0:-2])
    return numero


In [37]:
def get_pregao_anterior(dia, decrescimo):
    return datas_pregoes[datas_pregoes.index(dia) - decrescimo] if (datas_pregoes.index(dia) - decrescimo) > 0 else None

def calcula_media_movel(dados_pregao, dia, qtd_dias, tipo="aritimetica"):
    media = 0
    if tipo == "aritimetica":
        for i in range(qtd_dias):
            data = datas_pregoes[datas_pregoes.index(dia) - qtd_dias + 1]
            media += dados_pregao[data][4]
            
    return media/qtd_dias

def build_dataset(dados_pregao, dados_ibov):
    """
    Formato - > [abertura_papel, fechamento_anterior, variacao_anterior, volume_titulos_negociados, gap_baixa, gap_baixa, ]
    """
    dataset = []
    labels = []
    
    for dia in dados_pregao:
        
        if get_pregao_anterior(dia, 52) is None:
            continue
        
        dia_anterior1 = get_pregao_anterior(dia, 1)
        dia_anterior2 = get_pregao_anterior(dia, 2)
        dia_anterior3 = get_pregao_anterior(dia, 3)
        dia_anterior4 = get_pregao_anterior(dia, 4)
        
        if dia_anterior1 in dados_pregao and dia_anterior2 in dados_pregao \
        and dia_anterior3 in dados_pregao and dia_anterior4 in dados_pregao \
        and dia_anterior1 in dados_ibov and dia_anterior2 in dados_ibov \
        and dia_anterior3 in dados_ibov and dia_anterior4 in dados_ibov:
            linha = []
            
            # Fechamentos
            linha.append(dados_pregao[dia_anterior1][8])
            linha.append(dados_pregao[dia_anterior2][8])
            
            linha.append(dados_ibov[dia_anterior1][8])
            
            # Maxima e minima:
            linha.append(100 * (dados_pregao[dia_anterior1][4] - dados_pregao[dia_anterior1][1]) / dados_pregao[dia_anterior1][4])
            linha.append(100 * (dados_pregao[dia_anterior1][4] - dados_pregao[dia_anterior1][2]) / dados_pregao[dia_anterior1][4])
            
            # Volume:
            linha.append((dados_pregao[dia_anterior1][7] - dados_pregao[dia_anterior2][7]) / dados_pregao[dia_anterior1][7])

            # GAP:
            linha.append( 100 * (dados_pregao[dia][0] - dados_pregao[dia_anterior1][4]) / dados_pregao[dia_anterior1][4])
            
            mm20 = calcula_media_movel(dados_pregao, dia, 20)
            mm21 = calcula_media_movel(dados_pregao, dia, 21)
            mm50 = calcula_media_movel(dados_pregao, dia, 50)
            mm51 = calcula_media_movel(dados_pregao, dia, 51)
            
            # Distancias das médias móveis aritimeticas:
            linha.append(mm20  * 5 / dados_pregao[dia_anterior1][4])
            linha.append(mm50  * 5 / dados_pregao[dia_anterior1][4])
            
            # Médias moveis 
            linha.append((mm20 - mm21)  * 5 / mm20)
            linha.append((mm50 - mm51) * 5 / mm50) 
            
            # Label:
            labels.append([0,1] if dados_pregao[dia][0] >= dados_pregao[dia][4] else [1,0])
            
            dataset.append(linha)
    
    return dataset, labels


In [4]:
papeis = {}

for v in vet[1:-2]:
    extract_data(v)

In [38]:
import random

datas_pregoes = sorted(datas_pregoes)

dataset_oi = [[],[]]

# dataset_bbas4 = build_dataset(papeis['USIM5'], papeis['BOVA11'])

dataset_itsa4 = build_dataset(papeis['ITSA4'], papeis['BOVA11'])
dataset_itub4 = build_dataset(papeis['ITUB4'], papeis['BOVA11'])
# dataset_itsa3 = build_dataset(papeis['ITSA3'], papeis['BOVA11'])
dataset_itub3 = build_dataset(papeis['ITUB3'], papeis['BOVA11'])

# dataset_bbas3 = build_dataset(papeis['BBAS3'], papeis['BOVA11'])


dataset_oi[0] += dataset_itsa4[0]
dataset_oi[1] += dataset_itsa4[1]
dataset_oi[0] += dataset_itub4[0]
dataset_oi[1] += dataset_itub4[1]
# dataset_oi[0] += dataset_itsa3[0]
# dataset_oi[1] += dataset_itsa3[1]
dataset_oi[0] += dataset_itub3[0]
dataset_oi[1] += dataset_itub3[1]

# dataset_oi[0] += dataset_bbas3[0]
# dataset_oi[1] += dataset_bbas3[1]
# dataset_oi[0] += dataset_bbas4[0]
# dataset_oi[1] += dataset_bbas4[1]

z = list(zip(dataset_oi[1],dataset_oi[0]))
random.shuffle(z)
output_papeis, input_papeis = zip(*z)

output_papeis = list(output_papeis)
input_papeis = list(input_papeis)

print(len(output_papeis))

7257


In [ ]:
def verifica_altas_gap(dados_pregao):
    qtd_alta = 0
    qtd_baixa = 0
    
    for dia in dados_pregao:
        dia_anterior1 = get_pregao_anterior(dia, 1)
        if dia_anterior1 in dados_pregao:
            if dados_pregao[dia][0] > dados_pregao[dia_anterior1][4]:
                if dados_pregao[dia][8] > 0:
                    qtd_alta += 1
                else:
                    qtd_baixa+=1
    return qtd_alta / (qtd_alta + qtd_baixa)


def verifica_altas_alta_anterior(dados_pregao, dados_ibov):
    qtd_alta = 0
    qtd_baixa = 0
    
    for dia in dados_pregao:
        dia_anterior1 = get_pregao_anterior(dia, 1)
        dia_anterior2 = get_pregao_anterior(dia, 2)
        
        if dia_anterior1 in dados_pregao and dia_anterior2 in dados_pregao and \
           dia_anterior1 in dados_ibov and dia_anterior2 in dados_ibov:
            if dados_pregao[dia_anterior1][8] > 0 and dados_ibov[dia_anterior1][8] > 0:
                if dados_pregao[dia][8] > 0:
                    qtd_alta += 1
                else:
                    qtd_baixa+=1
    return qtd_alta / (qtd_alta + qtd_baixa)


print(verifica_altas(papeis['ITUB4']))
print(verifica_altas_alta_anterior(papeis['ITUB4'], papeis['BOVA11']))

## GRAFICOS

In [42]:
import plotly.graph_objs as go
import numpy as np
import statistics

# Graphs comparing distance
def plot_graph():
    fig = go.Figure()
#     fig.add_trace(go.Scatter(x=[j for j in range(len(dataset_oi[1]))], y=[10 if k==[1,0] else -10 for k in dataset_oi[1]], mode='markers', name='markers'))
    for i in range(11):
        fig.add_trace(go.Scatter(x=[j for j in range(len(dataset_oi[0]))], y=[dataset_oi[0][k][i] for k in range(len(dataset_oi[0]))] ))
    fig.show()

    
def plot_histogram(dados_pregao):
    x = []
    y = []
    z = []
    h = []
    for dia in dados_pregao:
        if dados_pregao[dia][8] > 0:
            x.append(100 * ( dados_pregao[dia][2] - dados_pregao[dia][0]) / dados_pregao[dia][0])
            y.append(dados_pregao[dia][8])   
        else:
            z.append(100 * ( dados_pregao[dia][1] - dados_pregao[dia][0]) / dados_pregao[dia][0])
            h.append(dados_pregao[dia][8])
            
    fig = go.Figure()
    
    fig.add_trace(go.Histogram(x=x,nbinsx=200,  name='% ganho no dia positivo'))
    fig.add_trace(go.Histogram(x=y,nbinsx=200, name='% variacao para baixo no dia positivo'))
    
    fig.add_trace(go.Histogram(x=z,nbinsx=200,  name='% perca no dia negativo'))
    fig.add_trace(go.Histogram(x=h,nbinsx=200, name='% variacao para cima no dia positivo'))
    fig.show()
    
    print("Média das altas: " + str(statistics.mean(y)))
    print("Média dos menores precos: " + str(statistics.mean(x)))
    
    print("Média das baixas: " + str(statistics.mean(z)))
    print("Média dos maiores precos: " + str(statistics.mean(h)))
    
    
# plot_histogram(papeis['ITUB4'])

plot_graph()

In [39]:
from numpy import loadtxt
from keras.models import Sequential
from keras.layers import Dense
from sklearn.metrics import confusion_matrix, accuracy_score

def model_keras(input_train, output_train, epochs, batch_size):
    # define the keras model
    
    model = Sequential()
    model.add(Dense(22, input_dim=11, activation='relu'))
    model.add(Dense(33, activation='relu'))
    model.add(Dense(22, activation='relu'))
    model.add(Dense(2, activation='sigmoid'))
    
    # compile the keras model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    model.summary()
    
    # fit the keras model on the dataset
    model.fit(input_train, output_train, epochs=epochs, batch_size=batch_size)
    
    return model

def evaluate_model(model, input_test, output_test):    
    # evaluate the keras model
    _, accuracy = model.evaluate(input_test, output_test)
    
    print('Accuracy: %.2f' % (accuracy*100))
    
    test_predictions = model.predict_classes(input_test)
    
    keras_test_output = [1 if out == [0,1] else 0 for out in output_test[0]]
    cm = confusion_matrix(y_true = keras_test_output, y_pred = test_predictions)
    print(cm)

In [41]:
# for i in range(1,500,50):
#     for j in range(1,20,2): 
#         print(i,j)

model = model_keras([input_papeis[0:7000]], [output_papeis[0:7000]], 100, 2)
evaluate_model(model, [input_papeis[7000:-1]], [output_papeis[7000:-1]])

Model: "sequential_11"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_34 (Dense)             (None, 22)                264       
_________________________________________________________________
dense_35 (Dense)             (None, 33)                759       
_________________________________________________________________
dense_36 (Dense)             (None, 22)                748       
_________________________________________________________________
dense_37 (Dense)             (None, 2)                 46        
Total params: 1,817
Trainable params: 1,817
Non-trainable params: 0
_________________________________________________________________
Epoch 1/100
7000/7000 [==============================] - 6s 907us/step - loss: 0.6970 - accuracy: 0.5071
Epoch 2/100
7000/7000 [==============================] - 7s 953us/step - loss: 0.6940 - accuracy: 0.5059
Epoch 3/100
7000/7000 [================

7000/7000 [==============================] - 7s 995us/step - loss: 0.6432 - accuracy: 0.6026
Epoch 71/100
7000/7000 [==============================] - 8s 1ms/step - loss: 0.6367 - accuracy: 0.6036
Epoch 72/100
7000/7000 [==============================] - 9s 1ms/step - loss: 0.6376 - accuracy: 0.6126
Epoch 73/100
7000/7000 [==============================] - 6s 884us/step - loss: 0.6399 - accuracy: 0.6104
Epoch 74/100
7000/7000 [==============================] - 6s 904us/step - loss: 0.6383 - accuracy: 0.6113
Epoch 75/100
7000/7000 [==============================] - 7s 1ms/step - loss: 0.6365 - accuracy: 0.6107
Epoch 76/100
7000/7000 [==============================] - 9s 1ms/step - loss: 0.6348 - accuracy: 0.6096
Epoch 77/100
7000/7000 [==============================] - 7s 991us/step - loss: 0.6333 - accuracy: 0.6122
Epoch 78/100
7000/7000 [==============================] - 8s 1ms/step - loss: 0.6318 - accuracy: 0.6136
Epoch 79/100
7000/7000 [==============================] - 9s 1ms/step

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import itertools

def plot_confusion_matrix(cm,
                          target_names,
                          title='Confusion matrix',
                          cmap=None,
                          normalize=True):
   
    accuracy = np.trace(cm) / np.sum(cm).astype('float')
    misclass = 1 - accuracy

    if cmap is None:
        cmap = plt.get_cmap('Blues')

    plt.figure(figsize=(8, 6))
    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()

    if target_names is not None:
        tick_marks = np.arange(len(target_names))
        plt.xticks(tick_marks, target_names, rotation=45)
        plt.yticks(tick_marks, target_names)

    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]


    thresh = cm.max() / 1.5 if normalize else cm.max() / 2
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        if normalize:
            plt.text(j, i, "{:0.4f}".format(cm[i, j]),
                     horizontalalignment="center",
                     color="white" if cm[i, j] > thresh else "black")
        else:
            plt.text(j, i, "{:,}".format(cm[i, j]),
                     horizontalalignment="center",
                     color="white" if cm[i, j] > thresh else "black")


    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label\naccuracy={:0.4f}; misclass={:0.4f}'.format(accuracy, misclass))
    plt.show()
    
m = np.array([[99, 47],
 [52, 61]])
plot_confusion_matrix(m,None)